# Biomass Yield and Spectral Trends

```
date: 2024-12-12
authors:
    - name: Brookie Guzder-Williams
affiliations:
    - University of California Berkeley, The Eric and Wendy Schmidt Center for Data Science & Environment
license: CC-BY-4.0
```

This notebook uses DSE's [Spectral Trend Database](https://github.com/SchmidtDSE/spectral_trend_database) (STDB) to
produce and interactive chart displaying Biomass Yield vs a number of different spectral incides over time.

1. Fetch Data for a random point: We use STDS's [query module](https://github.com/SchmidtDSE/spectral_trend_database/blob/main/spectral_trend_database/query.py) and in particular the [`QueryConstructor`](https://github.com/SchmidtDSE/spectral_trend_database/blob/54146cf058e2180829e2c169b37c18ddf62b68a0/spectral_trend_database/query.py#L21-L114) to generate a ...
2. Build Chart
3. Save Chart JSON to improve responsiveness of chart


---

### IMPORTS


In [1]:
from importlib import reload
from typing import Callable, Union, Optional, Literal, TypeAlias, Sequence, Any
import re
from pprint import pprint
import random
import pandas as pd
import numpy as np
import xarray as xr
import tensorflow as tf
from IPython.display import HTML
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt
from spectral_trend_database.config import config as c
from spectral_trend_database import query
from spectral_trend_database import utils
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn import metrics


---

### CONFIG

In [2]:
BQ_PREFIX = 'dse-regenag.BiomassTrends'
SAMPLE_FRAC = 0.0005
YEAR_START = 2008
YEAR_END = 2020
START_MMDD = '11-01'
END_MMDD = START_MMDD
ATTR_COLS = [
    'sample_id',
    'lon',
    'lat']
LIST_ATTRS = [
    'year',
    'biomass',
    'crop_type']
CHART_DATA_PATH = 'spectral_trends.chart_data.json'


---

### HELPER METHODS


In [3]:
def print_list(lst, max_len=7, view_size=3, sep=', ', connector=' ... '):
    size = len(lst)
    if size <= max_len:
        lst_str = sep.join(lst)
    else:
        head = sep.join(lst[:view_size])        
        tail = sep.join(lst[-view_size:])
        lst_str = f'{head}{connector}{tail}  [{size}]'
    print(lst_str)

def line(marker='-', length=100):
    print(marker*length)


---

### STDB DATABASE INFO

First we'll take a quick peak at the what is in the STDB database

In [4]:
YIELD_TABLE = 'SCYM_YIELD'
SMOOTHED_INDICES_TABLE = 'SMOOTHED_INDICES_V1'
IDENT_DATE_COLUMNS = ['sample_id', 'year', 'date']

In [5]:
COLUMN_NAMES = {}
print('DATABASE INFO')
line()
query = reload(query)
table_names = query.table_names()
print('TABLES:')
pprint(table_names)
for table_name in [YIELD_TABLE, SMOOTHED_INDICES_TABLE]:
    COLUMN_NAMES[table_name] = query.column_names(table_name, run_query=True)
    print(f'\n{table_name}:')
    print_list(COLUMN_NAMES[table_name])
line()

DATABASE INFO
----------------------------------------------------------------------------------------------------
TABLES:
['SMOOTHED_INDICES_V1',
 'INDICES_STATS_V1',
 'LANDSAT_RAW_MASKED',
 'RAW_INDICES_V1',
 'SAMPLE_POINTS',
 'INDICES_STATS_V1_GROWING_SEASON',
 'INDICES_STATS_V1_OFF_SEASON',
 'ADMINISTRATIVE_BOUNDARIES',
 'SCYM_YIELD',
 'MACD_INDICES_V1']

SCYM_YIELD:
biomass, crop_type, year, sample_id

SMOOTHED_INDICES_V1:
ndbr, ndvi, grvi ... sample_id, rdvi, year  [39]
----------------------------------------------------------------------------------------------------


In [6]:
INDICES = [c for c in COLUMN_NAMES[SMOOTHED_INDICES_TABLE] if c not in IDENT_DATE_COLUMNS]
print_list(INDICES)

ndbr, ndvi, grvi ... si, nli, rdvi  [36]



---

### 1. Fetch Data

In [7]:
qc = query.QueryConstructor('SAMPLE_POINTS', table_prefix=BQ_PREFIX)
qc.select('sample_id')
qc.append(f'WHERE RAND() < {SAMPLE_FRAC}')
sample_ids_df = query.run(sql=qc.sql(), print_sql=True)
sample_ids_df = sample_ids_df.drop_duplicates()
print('nb_samples:', sample_ids_df.shape[0])

[info] spectral_trend_database.query.run: SELECT sample_id FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` WHERE RAND() < 0.0005
nb_samples: 10


In [8]:
def fetch_yield_and_trend_data(
        year_start: int,
        year_end: Optional[int] = None,
        sample_id: Optional[Union[list[str], str]] = None,
        print_sql: Optional[bool] = False,
        limit: Optional[int] = None) -> pd.DataFrame:
    """
    Builds and Executes a SQL Query to get all data
    form a given set of sample_ids during a specified time 
    period.
    
    Args: 
        year_start (int): start year to select data
        year_end (Optional[int] = None): 
            last year to select data from (inclusive). if None use <year_start>
        sample_id (Optional[Union[list[str], str]] = None)
            sample_id or list of sample-ids of data to select. if none select 
            from all samples.
        print_sql (Optional[bool] = False)
        limit (Optional[int] = None)

    Returns:
        pd.DataFrame of smoothed-spectral-indices
    """
    if year_end is None: 
        year_end=year_start
    qc = query.QueryConstructor(
        'SAMPLE_POINTS', 
        table_prefix=BQ_PREFIX,
        using=['sample_id'],  
        how='inner')
    qc.join('SCYM_YIELD')
    qc.join('SMOOTHED_INDICES_V1', 'sample_id', 'year')
    if sample_id:
        if isinstance(sample_id, list):
            sample_id = [f"'{s}'" for s in sample_id]
            sample_ids = f'({", ".join(sample_id)})'
            qc.where(sample_id=sample_ids, sample_id_op='in')
        else:
            qc.where(sample_id=sample_id)
    qc.where('SMOOTHED_INDICES_V1', year=year_start, year_op='>=')
    qc.where('SMOOTHED_INDICES_V1', year=year_end, year_op='<=')
    df = query.run(sql=qc.sql(), print_sql=print_sql)
    return df

In [9]:
data = fetch_yield_and_trend_data(
    year_start=YEAR_START,
    year_end=YEAR_END,
    sample_id=sample_ids_df.sample_id.tolist(),
    print_sql=True)

print('shape:', data.shape)
data.sample(3)

[info] spectral_trend_database.query.run: SELECT * FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` INNER JOIN `dse-regenag.BiomassTrends.SCYM_YIELD` USING (sample_id) INNER JOIN `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1` USING (sample_id, year) WHERE `dse-regenag.BiomassTrends.SAMPLE_POINTS`.sample_id in ('9zg4c1qgqku', '9zmhp42txzr', '9zs4bx6nhpk', '9zv00u7vv7r', 'cbhb01bbyjy', 'dp0e5zwyq3r', 'dp0rw10qucn', 'dp1hxcshs9g', 'dp1z8bd5vje', 'dp2t1cqfz0z') AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year >= 2008 AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year <= 2020
shape: (122, 46)


sample_id  year geohash_5 geohash_7  geohash_9        lon        lat  \
17  9zmhp42txzr  2010     9zmhp   9zmhp42  9zmhp42tx -93.910104  41.497719   
97  dp1hxcshs9g  2019     dp1hx   dp1hxcs  dp1hxcshs -88.247483  40.175038   
38  9zv00u7vv7r  2008     9zv00   9zv00u7  9zv00u7vv -94.180406  43.618102   

    biomass crop_type                                               ndbr  ...  \
17     2338      corn  [0.8020385168710418, 0.761111421352999, 0.7212...  ...   
97      933       soy  [0.5416618662580623, 0.49794495603168176, 0.45...  ...   
38     2638      corn  [0.21655032309999994, 0.21167971548749995, 0.2...  ...   

                                                  msr  \
17  [2.833344026642882, 2.605392583520121, 2.39049...   
97  [1.3396010438805517, 1.2521736265218133, 1.168...   
38  [0.6532791573999996, 0.6442685212749997, 0.635...   

                                                  tvi  \
17  [1.18813572972331, 1.1612336370067855, 1.13585...   
97  [1.09283545107797, 1.0758940770811551, 1.05953...   
38  [0.9930999128428565, 0.9894172873374995, 0.985...   

                                                  si1  \
17  [0.04697344634080947, 0.05942996108841286, 0.0...   
97  [0.06444315995137456, 0.06569119617075751, 0.0...   
38  [0.0935228940142857, 0.0927293686375, 0.091935...   

                                                  rvi  \
17  [14.497812856094473, 13.271434815748242, 12.11...   
97  [5.3692832472491885, 5.032731062206502, 4.7142...   
38  [2.6917618916999997, 2.6678134904624997, 2.643...   

                                                 tdvi  \
17  [0.7922603813634755, 0.7408201033375185, 0.692...   
97  [0.3878954289539703, 0.36588399604133715, 0.34...   
38  [0.2954465449000001, 0.2910558050625001, 0.286...   

                                                osavi  \
17  [0.6888106469336722, 0.6450891646813475, 0.603...   
97  [0.4413680815141847, 0.41771976878131545, 0.39...   
38  [0.3245218118714285, 0.31988473388749994, 0.31...   

                                                   si  \
17  [0.030679068250658387, 0.043937479459377066, 0...   
97  [0.04954502843579181, 0.05067451694958326, 0.0...   
38  [0.07004421972857144, 0.06961416357500001, 0.0...   

                                                  nli  \
17  [0.8447933525916264, 0.7432393664406607, 0.646...   
97  [0.12229554748168381, 0.05837311643034407, -0....   
38  [-0.17554894249999992, -0.1866578000499999, -0...   

                                                 date  \
17  [2009-09-05T00:00:00.000000000, 2009-09-06T00:...   
97  [2018-09-02T00:00:00.000000000, 2018-09-03T00:...   
38  [2007-09-08T00:00:00.000000000, 2007-09-09T00:...   

                                                 rdvi  
17  [0.6436694696741146, 0.6028117506307256, 0.564...  
97  [0.37198273396544956, 0.3521462789494104, 0.33...  
38  [0.27629586752857144, 0.27233666763750003, 0.2...  

[3 rows x 46 columns]

In [10]:
rows = data[data.sample_id == data.sample().sample_id.iloc[0]]
rows = rows.sort_values('year').reset_index(drop=True)

In [11]:
utils = reload(utils)
def filter_dates(row):
    return dict(date=slice(f'{row.year-1}-{START_MMDD}', f'{row.year}-{END_MMDD}'))
    
ds = utils.rows_to_xr(
    rows, 
    coord='date', 
    sel=filter_dates, 
    attr_cols=ATTR_COLS,
    list_attrs=LIST_ATTRS)
ds

<xarray.Dataset>
Dimensions:   (date: 4395)
Coordinates:
  * date      (date) datetime64[ns] 2007-11-01 2007-11-02 ... 2019-11-01
Data variables: (12/36)
    ndbr      (date) float64 -0.1972 -0.196 -0.1941 ... 0.2481 0.2495 0.2509
    ndvi      (date) float64 0.1673 0.1652 0.1629 ... 0.2764 0.2667 0.2566
    grvi      (date) float64 1.702 1.684 1.665 1.645 ... 2.451 2.385 2.32 2.255
    ndwi      (date) float64 -0.2543 -0.2484 -0.2422 ... -0.4093 -0.3979 -0.3858
    slavi     (date) float64 0.4503 0.4501 0.4501 ... 0.7933 0.7765 0.7619
    ndmi      (date) float64 -0.2768 -0.2731 -0.2688 ... 0.008362 0.01423
    ...        ...
    rvi       (date) float64 1.409 1.404 1.399 1.393 ... 1.642 1.565 1.496 1.434
    tdvi      (date) float64 0.08235 0.08073 0.07905 ... 0.1372 0.1305 0.1241
    osavi     (date) float64 0.1015 0.09983 0.09806 ... 0.1672 0.1602 0.1532
    si        (date) float64 0.1032 0.1061 0.1094 0.113 ... 0.1254 0.1344 0.1441
    nli       (date) float64 -0.6237 -0.6243 -0.6246 ... -0.5074 -0.5128 -0.5168
    rdvi      (date) float64 0.0849 0.08348 0.08198 ... 0.1402 0.1343 0.1283
Attributes:
    sample_id:  cbhb01bbyjy
    lon:        -94.5690164606
    lat:        45.0097736326
    year:       [2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, ...
    biomass:    [669, 2844, 811, 2704, 693, 2268, 648, 3176, 836, 3459, 790, ...
    crop_type:  ['soy', 'corn', 'soy', 'corn', 'soy', 'corn', 'soy', 'corn', ...

In [12]:
yield_biomass = { y: b for y,b in zip(ds.year, ds.biomass)}
crop_types = { y: b for y,b in zip(ds.year, ds.crop_type)}
dvars = { k: ds[k].data for k in ds.data_vars }
_df = pd.DataFrame(dvars)
_df['date'] = ds.date.data
_df['idx'] = list(_df.index)
_df['year'] = _df.date.apply(lambda d: d.year)
_df['biomass'] = _df.year.apply(lambda y: yield_biomass.get(y, None))
_df['crop_type'] = _df.year.apply(lambda y: crop_types.get(y, 'soy'))

In [13]:
_df.date.astype(str)

0       2007-11-01
1       2007-11-02
2       2007-11-03
3       2007-11-04
4       2007-11-05
           ...    
4390    2019-10-28
4391    2019-10-29
4392    2019-10-30
4393    2019-10-31
4394    2019-11-01
Name: date, Length: 4395, dtype: object

In [14]:
# _df['date'] = _df.date.astype(str).apply(lambda d: f'{d}T00:00:01.000Z')
# _df['date'] = pd.to_datetime(_df.date.astype(str))
# _df.to_json(CHART_DATA_PATH, orient='records', lines=False)


---

### CHART

In [15]:
S = 1.25
DEFAULT_INDEX = 'ndvi'
HEIGHT = 400 * S
GRAPH_WIDTH = 600 * S
SI_COLOR = '#515e68'
SI_OPACITY = 0.6
YIELD_OPACITY = 0.5
TITLE_COLOR = '#333'
TITLE_SIZE = 22
TITLE_WEIGHT = 200
SUBTITLE_COLOR = '#aaa'
SUBTITLE_SIZE = 14
SOY_COLOR = '#4e9561'
CORN_COLOR = '#e2d644'

In [16]:
TITLE = 'SPECTRAL TRENDS'
SUBTITLE = 'exploring yield as a function of spectral indices'

In [17]:
chart_data = _df
# chart_data = CHART_DATA_PATH

In [18]:
#| label: nb.indices_vs_yield
#| placeholder: ./images/TBD.png

# alt.data_transformers.enable("vegafusion")

display(HTML("""
<style>
  span.vega-bind-name {
    color: #555;
    margin: 0 10px 0 60px;
    font-size: 20px;
  }
  .vega-bind label select {
    color: #555;
    font-size: 18px;
  }
</style>
"""))

# yield chart
yield_scale = alt.Scale(
    domain=[0.0, 3000],
    clamp=True
)
yield_color_scale = alt.Scale(
    domain=['soy', 'corn'], 
    range=[SOY_COLOR, CORN_COLOR])
yield_yaxis = alt.Axis(title='Biomass Yield', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
yield_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('biomass:Q', axis=yield_yaxis, scale=yield_scale),
    color=alt.Color('crop_type:N', scale=yield_color_scale)
).mark_area(
    filled=True,
    opacity=YIELD_OPACITY,
    interpolate='step-before')

# interactive spectral index chart
si_yaxis = alt.Axis(title='Spectral Index', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
si_dropdown = alt.binding_select(
    options=INDICES,
    labels=[n.upper() for n in INDICES],
    name='Spectral Index: '.upper()
)
ycol_param = alt.param(
    value=DEFAULT_INDEX,
    bind=si_dropdown
)
si_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('y:Q', axis=si_yaxis)
).properties(
    width=GRAPH_WIDTH,
    height=HEIGHT
).transform_calculate(
    y=f'datum[{ycol_param.name}]'
).add_params(
    ycol_param
).mark_area(
    fill=SI_COLOR,
    fillOpacity=SI_OPACITY
)

# display
title = alt.Title(
    TITLE,
    color=TITLE_COLOR,
    fontSize=TITLE_SIZE,
    fontWeight=TITLE_WEIGHT,
    subtitle=SUBTITLE,
    subtitleColor=SUBTITLE_COLOR,
    subtitleFontSize=SUBTITLE_SIZE)

chart = alt.layer(yield_chart, si_chart).resolve_scale(y='independent')
chart = chart.properties(
    title=title).configure_legend(
    title=None,
    labelFontSize=18,  
    labelColor=SUBTITLE_COLOR 
).interactive()
chart 

alt.LayerChart(...)